In [9]:
import numpy as np
from scipy.io import loadmat
from scipy.optimize import minimize
from sklearn import svm
import matplotlib.pyplot as plt


def preprocess():
    """ 
     Input:
     Although this function doesn't have any input, you are required to load
     the MNIST data set from file 'mnist_all.mat'.

     Output:
     train_data: matrix of training set. Each row of train_data contains 
       feature vector of a image
     train_label: vector of label corresponding to each image in the training
       set
     validation_data: matrix of training set. Each row of validation_data 
       contains feature vector of a image
     validation_label: vector of label corresponding to each image in the 
       training set
     test_data: matrix of training set. Each row of test_data contains 
       feature vector of a image
     test_label: vector of label corresponding to each image in the testing
       set
    """

    mat = loadmat('mnist_all.mat')  # loads the MAT object as a Dictionary

    n_feature = mat.get("train1").shape[1]
    n_sample = 0
    for i in range(10):
        n_sample = n_sample + mat.get("train" + str(i)).shape[0]
    n_validation = 1000
    n_train = n_sample - 10 * n_validation

    # Construct validation data
    validation_data = np.zeros((10 * n_validation, n_feature))
    for i in range(10):
        validation_data[i * n_validation:(i + 1) * n_validation, :] = mat.get("train" + str(i))[0:n_validation, :]

    # Construct validation label
    validation_label = np.ones((10 * n_validation, 1))
    for i in range(10):
        validation_label[i * n_validation:(i + 1) * n_validation, :] = i * np.ones((n_validation, 1))

    # Construct training data and label
    train_data = np.zeros((n_train, n_feature))
    train_label = np.zeros((n_train, 1))
    temp = 0
    for i in range(10):
        size_i = mat.get("train" + str(i)).shape[0]
        train_data[temp:temp + size_i - n_validation, :] = mat.get("train" + str(i))[n_validation:size_i, :]
        train_label[temp:temp + size_i - n_validation, :] = i * np.ones((size_i - n_validation, 1))
        temp = temp + size_i - n_validation

    # Construct test data and label
    n_test = 0
    for i in range(10):
        n_test = n_test + mat.get("test" + str(i)).shape[0]
    test_data = np.zeros((n_test, n_feature))
    test_label = np.zeros((n_test, 1))
    temp = 0
    for i in range(10):
        size_i = mat.get("test" + str(i)).shape[0]
        test_data[temp:temp + size_i, :] = mat.get("test" + str(i))
        test_label[temp:temp + size_i, :] = i * np.ones((size_i, 1))
        temp = temp + size_i

    # Delete features which don't provide any useful information for classifiers
    sigma = np.std(train_data, axis=0)
    index = np.array([])
    for i in range(n_feature):
        if (sigma[i] > 0.001):
            index = np.append(index, [i])
    train_data = train_data[:, index.astype(int)]
    validation_data = validation_data[:, index.astype(int)]
    test_data = test_data[:, index.astype(int)]

    # Scale data to 0 and 1
    train_data /= 255.0
    validation_data /= 255.0
    test_data /= 255.0

    return train_data, train_label, validation_data, validation_label, test_data, test_label


def sigmoid(z):
    return 1.0 / (1.0 + np.exp(-z))


def blrObjFunction(initialWeights, *args):
    """
    blrObjFunction computes 2-class Logistic Regression error function and
    its gradient.

    Input:
        initialWeights: the weight vector (w_k) of size (D + 1) x 1 
        train_data: the data matrix of size N x D
        labeli: the label vector (y_k) of size N x 1 where each entry can be either 0 or 1 representing the label of corresponding feature vector

    Output: 
        error: the scalar value of error function of 2-class logistic regression
        error_grad: the vector of size (D+1) x 1 representing the gradient of
                    error function
    """
    train_data, labeli = args

    n_data = train_data.shape[0]
    n_features = train_data.shape[1]
    error = 0
    error_grad = np.zeros((n_features + 1, 1))

    ##################
    # YOUR CODE HERE #
    ##################
    # HINT: Do not forget to add the bias term to your input data
    

    features_new = n_features + 1
    w = initialWeights.reshape((features_new,1))
    bias = np.ones((n_data,1))
#     print(bias)
#     print(w)  
    x = np.hstack((bias,train_data))
#     print(x)
    z = np.dot(x,w)
    theta = sigmoid(z)
#     print("sigmoid",theta) 
    first = labeli * np.log(theta)
    second = (1.0 - labeli) * np.log(1.0 - theta)
    numerator = -np.sum(first + second)
    denominator = n_data
    error = numerator / denominator
#     print("Error value ",error)
    error_grad = (theta - labeli) * x
    error_grad = np.sum(error_grad, axis=0) / n_data
#     print("error_grad",error_grad)
    
    return error, error_grad

def blrPredict(W, data):
    """
     blrObjFunction predicts the label of data given the data and parameter W 
     of Logistic Regression
     
     Input:
         W: the matrix of weight of size (D + 1) x 10. Each column is the weight 
         vector of a Logistic Regression classifier.
         X: the data matrix of size N x D
         
     Output: 
         label: vector of size N x 1 representing the predicted label of 
         corresponding feature vector given in data matrix

    """
    label = np.zeros((data.shape[0], 1))

    ##################
    # YOUR CODE HERE #
    ##################
    # HINT: Do not forget to add the bias term to your input data
    
    bias = np.ones((data.shape[0],1))
    d = np.hstack((bias,data))
    z = np.dot(d,W)
    label = sigmoid(z)
    label = np.argmax(label, axis = 1) 
    label = label.reshape((data.shape[0], 1))
    

    return label

def mlrObjFunction(params, *args):
    """
    mlrObjFunction computes multi-class Logistic Regression error function and
    its gradient.
    Input:
        initialWeights_b: the weight vector of size (D + 1) x 10
        train_data: the data matrix of size N x D
        labeli: the label vector of size N x 1 where each entry can be either 0 or 1
                representing the label of corresponding feature vector
    Output:
        error: the scalar value of error function of multi-class logistic regression
        error_grad: the vector of size (D+1) x 10 representing the gradient of
                    error function
    """
    train_data, labeli = args
    n_data = train_data.shape[0]
    n_feature = train_data.shape[1]
    error = 0
    error_grad = np.zeros((n_feature + 1, n_class))

    ##################
    # YOUR CODE HERE #
    ##################
    # HINT: Do not forget to add the bias term to your input data
    
    bias = np.ones((n_data,1))
    x = np.hstack((bias,train_data))
    features_new = n_feature + 1
    w = params.reshape((features_new,n_class))
    prod = np.dot(x , w)
    numerator = np.exp(prod)
    denominator = np.sum((np.exp(prod)),axis = 1).reshape(n_data , 1)
    theta = numerator / denominator
    y = labeli * np.log(theta)
    error = (-1 * np.sum(np.sum(y))) / n_data
    error_grad = (np.dot(x.T, (theta - labeli))) / n_data
    
    return error, error_grad.flatten()

def mlrPredict(W, data):
    """
     mlrObjFunction predicts the label of data given the data and parameter W
     of Logistic Regression

     Input:
         W: the matrix of weight of size (D + 1) x 10. Each column is the weight
         vector of a Logistic Regression classifier.
         X: the data matrix of size N x D

     Output:
         label: vector of size N x 1 representing the predicted label of
         corresponding feature vector given in data matrix

    """
    label = np.zeros((data.shape[0], 1))

    ##################
    # YOUR CODE HERE #
    ##################
    # HINT: Do not forget to add the bias term to your input data
    size = data.shape[0]
    bias = np.ones((size,1))
    x = np.hstack((bias,data))
    prod = np.dot(x,W)
    num = np.exp(prod)
    denom = np.sum(np.exp(prod))
    label = num / denom
    label = np.argmax(label, axis=1)
    label = label.reshape((size,1))

    return label

train_data, train_label, validation_data, validation_label, test_data, test_label = preprocess()

# number of classes
n_class = 10

# number of training samples
n_train = train_data.shape[0]

# number of features
n_feature = train_data.shape[1]

Y = np.zeros((n_train, n_class))
for i in range(n_class):
    Y[:, i] = (train_label == i).astype(int).ravel()

# Logistic Regression with Gradient Descent
W = np.zeros((n_feature + 1, n_class))
initialWeights = np.zeros((n_feature + 1, 1))
opts = {'maxiter': 100}
for i in range(n_class):
    labeli = Y[:, i].reshape(n_train, 1)
    args = (train_data, labeli)
    nn_params = minimize(blrObjFunction, initialWeights, jac=True, args=args, method='CG', options=opts)
    W[:, i] = nn_params.x.reshape((n_feature + 1,))

# Find the accuracy on Training Dataset
predicted_label = blrPredict(W, train_data)
print('\n Training set Accuracy:' + str(100 * np.mean((predicted_label == train_label).astype(float))) + '%')

# Find the accuracy on Validation Dataset
predicted_label = blrPredict(W, validation_data)
print('\n Validation set Accuracy:' + str(100 * np.mean((predicted_label == validation_label).astype(float))) + '%')

# Find the accuracy on Testing Dataset
predicted_label = blrPredict(W, test_data)
print('\n Testing set Accuracy:' + str(100 * np.mean((predicted_label == test_label).astype(float))) + '%')


# FOR EXTRA CREDIT ONLY
W_b = np.zeros((n_feature + 1, n_class))
initialWeights_b = np.zeros((n_feature + 1, n_class))
opts_b = {'maxiter': 100}

args_b = (train_data, Y)
nn_params = minimize(mlrObjFunction, initialWeights_b, jac=True, args=args_b, method='CG', options=opts_b)
W_b = nn_params.x.reshape((n_feature + 1, n_class))

# Find the accuracy on Training Dataset
predicted_label_b = mlrPredict(W_b, train_data)
print('\n Training set Accuracy:' + str(100 * np.mean((predicted_label_b == train_label).astype(float))) + '%')

# Find the accuracy on Validation Dataset
predicted_label_b = mlrPredict(W_b, validation_data)
print('\n Validation set Accuracy:' + str(100 * np.mean((predicted_label_b == validation_label).astype(float))) + '%')

# Find the accuracy on Testing Dataset
predicted_label_b = mlrPredict(W_b, test_data)
print('\n Testing set Accuracy:' + str(100 * np.mean((predicted_label_b == test_label).astype(float))) + '%')

error_grad [  4.01540000e-01   4.94117647e-06   1.84313725e-05   8.47058824e-06
   3.52941176e-07   6.27450980e-07   2.15686275e-06   2.18431373e-05
   5.31372549e-05   8.92549020e-05   1.29058824e-04   2.60078431e-04
   3.23372549e-04   3.48039216e-04   3.60901961e-04   4.03725490e-04
   3.60549020e-04   3.74941176e-04   3.17764706e-04   1.99647059e-04
   1.50196078e-04   1.08666667e-04   3.95686275e-05   1.26274510e-05
   5.88235294e-07   2.50980392e-06  -6.27450980e-07   1.32941176e-05
   1.22352941e-05   1.02156863e-04   2.99411765e-04   5.43176471e-04
   1.03392157e-03   1.79576471e-03   2.64403922e-03   3.75768627e-03
   5.07890196e-03   6.41862745e-03   7.11788235e-03   7.01254902e-03
   6.31388235e-03   5.32356863e-03   3.98231373e-03   2.41172549e-03
   1.28564706e-03   6.09960784e-04   1.92235294e-04   7.67843137e-05
   2.03137255e-05   7.60784314e-06   7.17647059e-06   2.11372549e-05
   1.08784314e-04   3.99960784e-04   1.09254902e-03   2.29305882e-03
   4.46396078e-03   7.1

error_grad [  4.01540000e-01   4.94117647e-06   1.84313725e-05   8.47058824e-06
   3.52941176e-07   6.27450980e-07   2.15686275e-06   2.18431373e-05
   5.31372549e-05   8.92549020e-05   1.29058824e-04   2.60078431e-04
   3.23372549e-04   3.48039216e-04   3.60901961e-04   4.03725490e-04
   3.60549020e-04   3.74941176e-04   3.17764706e-04   1.99647059e-04
   1.50196078e-04   1.08666667e-04   3.95686275e-05   1.26274510e-05
   5.88235294e-07   2.50980392e-06  -6.27450980e-07   1.32941176e-05
   1.22352941e-05   1.02156863e-04   2.99411765e-04   5.43176471e-04
   1.03392157e-03   1.79576471e-03   2.64403922e-03   3.75768627e-03
   5.07890196e-03   6.41862745e-03   7.11788235e-03   7.01254902e-03
   6.31388235e-03   5.32356863e-03   3.98231373e-03   2.41172549e-03
   1.28564706e-03   6.09960784e-04   1.92235294e-04   7.67843137e-05
   2.03137255e-05   7.60784314e-06   7.17647059e-06   2.11372549e-05
   1.08784314e-04   3.99960784e-04   1.09254902e-03   2.29305882e-03
   4.46396078e-03   7.1

error_grad [ -9.12941715e-02   9.75665955e-08   3.50999178e-07   1.52857599e-07
   6.36906662e-09   3.06070397e-09   1.24767016e-08   3.34384076e-07
   7.31450036e-07   1.69970169e-06   2.04788432e-06   3.53262153e-06
  -6.38593350e-06  -1.60162915e-05  -3.82172032e-06   5.91415881e-06
   5.74766625e-06   6.06588171e-06   3.63893808e-06   1.63886294e-06
   1.71200801e-06   1.19288367e-06   2.59578728e-07   6.16518567e-08
   4.40420082e-09   2.76507254e-09  -2.25365434e-06  -6.22594042e-07
   8.44870054e-08  -5.20825486e-06  -1.07503504e-05   5.07616863e-06
   1.31406967e-05   2.34830245e-05   2.30132531e-05   1.86980944e-05
   1.53151998e-05   4.96377609e-05   5.53201460e-05   5.02728647e-05
   5.25815509e-05   4.04750624e-05   2.24022718e-05   1.74664598e-05
   8.65427964e-06   4.76591286e-06   1.37704241e-06   3.59602197e-07
   5.77575862e-08   1.44751063e-08  -6.44806913e-06  -1.68650523e-06
  -8.62889270e-06  -1.01456520e-07  -7.36164000e-06  -2.89568265e-05
  -5.36508557e-05  -1.4

error_grad [ -9.16176935e-02   2.50989637e-08   9.95022969e-08   4.95691955e-08
   2.06538314e-09   1.41378761e-09   6.09941778e-09   2.00350376e-07
   4.51312028e-07   9.37365506e-07   1.27084995e-06   2.11828192e-06
  -7.88748448e-06  -1.79423714e-05  -6.17315809e-06   3.89697647e-06
   3.32265337e-06   3.82717729e-06   2.10044290e-06   6.87420451e-07
   7.37475989e-07   5.08241795e-07   8.28749575e-08   1.39098821e-08
   8.56908740e-10   1.24287329e-09  -2.24202389e-06  -7.08829543e-07
   7.16364873e-08  -4.56713311e-06  -1.14651709e-05   3.32114835e-06
   1.09890156e-05   1.77654759e-05   1.35294458e-05   4.50237631e-06
  -3.99385054e-06   2.66433771e-05   2.88334975e-05   2.52556049e-05
   3.09849131e-05   2.23432691e-05   1.12151498e-05   1.19538127e-05
   6.10342907e-06   3.28110487e-06   1.01902258e-06   2.11911706e-07
   2.55290651e-08   3.72840842e-09  -6.39546893e-06  -1.59960860e-06
  -8.15668297e-06  -5.45990579e-08  -8.26517841e-06  -3.27084522e-05
  -6.21003703e-05  -1.5

error_grad [ -2.17091591e-02   1.14318797e-10   7.32371414e-10   5.36432389e-10
   2.23513496e-11   6.40942405e-11   3.76150543e-10   5.30837400e-08
   1.87573371e-07   3.82460714e-07   1.14875023e-06   3.86885914e-06
  -5.01096939e-06  -1.70682609e-05  -6.15727215e-06   8.91739323e-06
   9.76494009e-06   1.50876139e-05   5.25198681e-06   3.74845100e-07
   6.81511647e-08   4.25732791e-08   5.91997340e-09   5.75113096e-10
   1.21414547e-12   5.06855663e-11  -1.97496320e-06  -6.67018175e-07
   3.08529188e-07   6.33705079e-06  -1.04964316e-06   1.46626620e-05
   3.84129328e-05   5.66384649e-05   5.77355551e-05   5.68573100e-05
   7.14742943e-05   1.52220870e-04   1.53588666e-04   1.34819356e-04
   1.19381165e-04   8.85151947e-05   5.55067463e-05   2.73745667e-05
   9.88877103e-06   3.87991719e-06   1.55601021e-06   1.31767558e-07
   2.48585942e-09   1.13113189e-10  -5.43738067e-06  -5.41132820e-07
   1.09730749e-05   2.52599795e-05   3.68179532e-05   3.37483118e-05
   6.92583242e-05   8.8

...

error_grad [  1.92985501e-03   4.98586688e-07   1.07318338e-06  -2.06420876e-08
  -8.60086983e-10   7.71537506e-09   2.33030996e-08   2.53622732e-07
   5.09401728e-07   6.38049093e-07   2.38153366e-06   9.52969102e-06
   1.20406175e-05   2.29090523e-05   2.83981971e-05   3.81454568e-05
   4.04627990e-05   2.83037956e-05   4.26847010e-05   2.62991975e-05
   2.24203661e-05   1.44501705e-05   5.97774146e-06   8.72802259e-07
   5.18808090e-08   5.63306944e-10   4.90909693e-09   5.61491586e-07
   1.52082989e-07   9.85351656e-07   2.91028774e-06   1.24418370e-06
  -1.96546495e-05  -5.83422605e-06   2.10855941e-05   1.13052784e-04
   2.05073340e-04   2.55174677e-04   2.44980686e-04   2.35208998e-04
   2.28207165e-04   2.03573989e-04   1.84668868e-04   1.22227547e-04
   7.56140568e-05   5.27074407e-05   2.03520740e-05   4.21548616e-06
   1.43507530e-08   3.44847024e-08   4.35663619e-08   5.85469049e-07
   4.15570775e-06   3.15922293e-06  -1.65193211e-05  -7.23714783e-05
  -2.00026542e-04  -2.2

error_grad [  3.28209097e-03   5.02649570e-07   1.08143248e-06  -2.13623051e-08
  -8.90096045e-10   8.23221816e-09   2.48865726e-08   2.75091376e-07
   5.53127977e-07   7.08885599e-07   2.55140105e-06   1.02498878e-05
   1.30717768e-05   2.45978605e-05   3.01368483e-05   3.99148976e-05
   4.25737694e-05   3.01937608e-05   4.43589469e-05   2.72168016e-05
   2.31580337e-05   1.48709332e-05   5.91920223e-06   8.53340438e-07
   5.12548860e-08   5.92752628e-10   5.15906054e-09   6.05967638e-07
   1.71360468e-07   1.03073342e-06   3.20356885e-06   3.05992596e-06
  -1.53822117e-05   5.45630222e-07   3.10556495e-05   1.28331342e-04
   2.25724596e-04   2.79941334e-04   2.69281222e-04   2.57366781e-04
   2.47303614e-04   2.19339957e-04   1.93727926e-04   1.27095696e-04
   7.78557472e-05   5.34075720e-05   2.04730805e-05   4.21581943e-06
   8.54162151e-09   3.86568716e-08   4.74120351e-08   6.23478712e-07
   4.61419702e-06   4.40673777e-06  -1.26532690e-05  -6.03745600e-05
  -1.74695844e-04  -1.7

error_grad [  7.18347819e-03   5.13685876e-07   1.10375078e-06  -2.34181217e-08
  -9.75755072e-10   9.79274673e-09   2.96801272e-08   3.42918758e-07
   6.92350282e-07   9.31269752e-07   3.07075595e-06   1.24739114e-05
   1.62895185e-05   2.97800229e-05   3.53733053e-05   4.52409627e-05
   4.87410190e-05   3.57056772e-05   4.92703130e-05   2.99684510e-05
   2.52909273e-05   1.60665502e-05   5.80068100e-06   8.04054748e-07
   4.96131749e-08   6.79456926e-10   5.90892099e-09   7.46897581e-07
   2.37636664e-07   1.16433990e-06   4.07971557e-06   8.00307883e-06
  -3.52072850e-06   1.90248199e-05   6.05739256e-05   1.74013119e-04
   2.87859132e-04   3.54491459e-04   3.43148176e-04   3.24857287e-04
   3.05140443e-04   2.66707600e-04   2.21259795e-04   1.41812530e-04
   8.46600590e-05   5.55383222e-05   2.08442388e-05   4.22151753e-06
  -8.84613339e-09   5.24860691e-08   5.96426474e-08   7.42252539e-07
   5.91408312e-06   7.56722354e-06  -2.74389968e-06  -2.94454795e-05
  -1.08991224e-04  -7.0

error_grad [  5.79446214e-03   4.55600475e-07   9.71419908e-07  -2.91422660e-08
  -1.21426108e-09   8.89420021e-09   2.70307188e-08   3.37499461e-07
   6.76372885e-07   8.26256211e-07   2.85721970e-06   1.19875169e-05
   1.57523705e-05   2.89086611e-05   3.36684669e-05   4.18490324e-05
   4.50570821e-05   3.08253493e-05   4.46997202e-05   2.73731318e-05
   2.37157438e-05   1.51173691e-05   5.06930024e-06   6.60436964e-07
   4.13782154e-08   5.79008120e-10   5.45524825e-09   7.19850692e-07
   2.39454865e-07   1.01091496e-06   3.88349434e-06   7.37118809e-06
  -5.55629881e-06   1.52535633e-05   5.32766823e-05   1.61660388e-04
   2.68355097e-04   3.26223760e-04   3.09187468e-04   2.89827988e-04
   2.74785788e-04   2.39914517e-04   1.98938641e-04   1.27182720e-04
   7.51364771e-05   4.94014033e-05   1.80560969e-05   3.43863355e-06
  -9.68004241e-08   5.15687588e-08   5.52668162e-08   6.97090278e-07
   5.63728967e-06   6.86612253e-06  -4.66994839e-06  -3.43407025e-05
  -1.19200462e-04  -8.5

KeyboardInterrupt: 